In [2]:
import pandas as pd
import numpy as np
import pickle as pkl

## Read dataset

In [3]:
game_data = pd.read_pickle("../flatten_games.pickle")
game_data

{'https://www.baseball-reference.com/boxes/CHN/CHN201504050.shtml': {'game_page_url': 'https://www.baseball-reference.com/boxes/CHN/CHN201504050.shtml',
  'have_att': True,
  'start_time': datetime.datetime(2015, 4, 5, 19, 17),
  'day': 'Sunday',
  'month': 'April',
  'is_federal_holiday': 0,
  'duration': datetime.timedelta(seconds=11040),
  'venue': 'Wrigley Field',
  'at_night': True,
  'on_grass': True,
  'weather_description': ' 44° F, Wind 7mph in from Centerfield, Sunny.',
  'temperature': 44,
  'wind_speed': 7,
  'weather': 'in Dome',
  'precipitation': 3,
  'umpires': ' HP - Mike Winters, 1B - Mark Wegner, 2B - Marty Foster, 3B - Mike Muchlinski.',
  'attendance': 35055,
  'team1_name': 'StLouisCardinals',
  'team1_pre_win': 0,
  'team1_pre_loss': 0,
  'team1_pre_win_pct': 0,
  'players':                          Batting AB  R  H RBI BB SO PA    BA   OBP  ...  \
  0               Dexter Fowler CF  4  0  1   0  0  2  4  .250  .250  ...   
  1                 Jorge Soler RF  4  

In [4]:
players_data = pd.read_pickle("../player-salaries.pickle")
players_data

{2017: {'ARI':                  Name       Salary AllStartAppearance
  0          Nick Ahmed     $566,000                   
  2        Jake Barrett     $548,300                   
  3       Gregor Blanco   $1,000,000                   
  5      Archie Bradley     $544,100                   
  6       Andrew Chafin     $559,300                   
  7      Patrick Corbin   $3,950,000                   
  8    Jorge De La Rosa   $2,250,000                   
  10    Randall Delgado   $1,775,000                   
  11    Daniel Descalso   $1,350,000                   
  12      Brandon Drury     $553,900                   
  15   Paul Goldschmidt   $8,875,000           All-Star
  16       Zack Greinke  $34,000,000           All-Star
  17  Jeremy Hazelbaker   $1,082,000                   
  19     Chris Herrmann     $937,500                   
  20        J.J. Hoover     $900,000                   
  21     Chris Iannetta   $1,500,000                   
  23          Jake Lamb     $573,30

## preprocessing

In [5]:
players_data.keys()

dict_keys([2017, 2018, 2019, 2020, 2021, 2022])

In [6]:
teams_2017 = players_data[2017].keys()
teams_2018 = players_data[2018].keys()
teams_2019 = players_data[2019].keys()
teams_2021 = players_data[2021].keys()
teams_2022 = players_data[2022].keys()

In [7]:
def get_player_salary_by_year(players_data_year):
    teams = players_data_year.keys()
    df_player_salary = pd.DataFrame()
    for team in teams:
        df_player_salary = pd.concat([df_player_salary, players_data_year[team]])

    df_player_salary['Salary'] = df_player_salary['Salary'].str.replace('$', '')
    df_player_salary['Salary'] = df_player_salary['Salary'].str.replace(',', '')
    df_player_salary['Salary'] = pd.to_numeric(df_player_salary['Salary'])
    print(df_player_salary.shape)
    return df_player_salary

In [8]:
players_2017 = get_player_salary_by_year(players_data[2017])
players_2017.head()

(840, 3)


C:\Users\gary6\AppData\Local\Temp\ipykernel_20176\1882614535.py:7: FutureWarning: The default value of regex will change from True to False in a future version. In addition, single character regular expressions will *not* be treated as literal strings when regex=True.
  df_player_salary['Salary'] = df_player_salary['Salary'].str.replace('$', '')


Name     Salary AllStartAppearance
0      Nick Ahmed   566000.0                   
2    Jake Barrett   548300.0                   
3   Gregor Blanco  1000000.0                   
5  Archie Bradley   544100.0                   
6   Andrew Chafin   559300.0

In [9]:
players_2018 = get_player_salary_by_year(players_data[2018])
players_2019 = get_player_salary_by_year(players_data[2019])
players_2021 = get_player_salary_by_year(players_data[2021])
players_2022 = get_player_salary_by_year(players_data[2022])

(816, 3)
(889, 3)
(571, 3)
(559, 3)


C:\Users\gary6\AppData\Local\Temp\ipykernel_20176\1882614535.py:7: FutureWarning: The default value of regex will change from True to False in a future version. In addition, single character regular expressions will *not* be treated as literal strings when regex=True.
  df_player_salary['Salary'] = df_player_salary['Salary'].str.replace('$', '')
C:\Users\gary6\AppData\Local\Temp\ipykernel_20176\1882614535.py:7: FutureWarning: The default value of regex will change from True to False in a future version. In addition, single character regular expressions will *not* be treated as literal strings when regex=True.
  df_player_salary['Salary'] = df_player_salary['Salary'].str.replace('$', '')
C:\Users\gary6\AppData\Local\Temp\ipykernel_20176\1882614535.py:7: FutureWarning: The default value of regex will change from True to False in a future version. In addition, single character regular expressions will *not* be treated as literal strings when regex=True.
  df_player_salary['Salary'] = df_p

## Select players by salary

In [10]:
salary_threshold = 30000000

In [11]:
players_salary_2017 = players_2017[players_2017['Salary'] > salary_threshold]
players_salary_2018 = players_2018[players_2018['Salary'] > salary_threshold]
players_salary_2019 = players_2019[players_2019['Salary'] > salary_threshold]
players_salary_2021 = players_2021[players_2021['Salary'] > salary_threshold]
players_salary_2022 = players_2022[players_2022['Salary'] > salary_threshold]
print(players_salary_2017.shape, players_salary_2018.shape, players_salary_2019.shape, players_salary_2021.shape, players_salary_2022.shape)

(2, 3) (3, 3) (6, 3) (11, 3) (13, 3)


In [12]:
def merge_players(players_list):
    df_players = pd.DataFrame(columns=['Name', 'Salary', 'AllStartAppearance'])
    for players in players_list:
        df_players = df_players.merge(players, on='Name', how='outer')
    df_players = df_players[['Name']]
    return df_players

In [105]:
df_players = merge_players([players_salary_2017, players_salary_2018, players_salary_2019, players_salary_2021, players_salary_2022])
print(df_players.shape)
df_players.head()

(16, 1)


C:\Users\gary6\AppData\Local\Temp\ipykernel_20968\754067190.py:4: FutureWarning: Passing 'suffixes' which cause duplicate columns {'AllStartAppearance_x', 'Salary_x'} in the result is deprecated and will raise a MergeError in a future version.
  df_players = df_players.merge(players, on='Name', how='outer')
C:\Users\gary6\AppData\Local\Temp\ipykernel_20968\754067190.py:4: FutureWarning: Passing 'suffixes' which cause duplicate columns {'AllStartAppearance_x', 'Salary_x'} in the result is deprecated and will raise a MergeError in a future version.
  df_players = df_players.merge(players, on='Name', how='outer')


Name
0     Zack Greinke
1  Clayton Kershaw
2       Mike Trout
3      David Price
4     Max Scherzer

In [106]:
df_players.to_csv(f'../data/players/players_salary_{salary_threshold}.csv', index=False)

## select players by all star

In [62]:
players_star_2017 = players_2017[players_2017['AllStartAppearance'] == "All-Star"].reset_index(drop=True)[['Name']]
players_star_2018 = players_2018[players_2018['AllStartAppearance'] == "All-Star"].reset_index(drop=True)[['Name']]
players_star_2019 = players_2019[players_2019['AllStartAppearance'] == "All-Star"].reset_index(drop=True)[['Name']]
players_star_2021 = players_2021[players_2021['AllStartAppearance'] == "All-Star"].reset_index(drop=True)[['Name']]
players_star_2022 = players_2022[players_2022['AllStartAppearance'] == "All-Star"].reset_index(drop=True)[['Name']]

In [63]:
print(players_star_2017.shape)
players_star_2017.head()

(71, 1)


Name
0  Paul Goldschmidt
1      Zack Greinke
2         Jake Lamb
3        Robbie Ray
4    Ender Inciarte

In [64]:
df_players = merge_players([players_star_2017, players_star_2018, players_star_2019, players_star_2021, players_star_2022])
print(df_players.shape)
df_players.head()

(246, 1)


Name
0  Paul Goldschmidt
1      Zack Greinke
2         Jake Lamb
3        Robbie Ray
4    Ender Inciarte

In [65]:
df_players.to_csv('../data/players/players_all_star.csv', index=False)

## select by salary and all star

In [13]:
salary_threshold = 5000000

In [14]:
players_salary_2017 = players_2017[players_2017['Salary'] > salary_threshold]
players_salary_2018 = players_2018[players_2018['Salary'] > salary_threshold]
players_salary_2019 = players_2019[players_2019['Salary'] > salary_threshold]
players_salary_2021 = players_2021[players_2021['Salary'] > salary_threshold]
players_salary_2022 = players_2022[players_2022['Salary'] > salary_threshold]
print(players_salary_2017.shape, players_salary_2018.shape, players_salary_2019.shape, players_salary_2021.shape, players_salary_2022.shape)

(248, 3) (241, 3) (228, 3) (200, 3) (229, 3)


In [15]:
players_star_2017 = players_salary_2017[players_salary_2017['AllStartAppearance'] == "All-Star"].reset_index(drop=True)[['Name']]
players_star_2018 = players_salary_2018[players_salary_2018['AllStartAppearance'] == "All-Star"].reset_index(drop=True)[['Name']]
players_star_2019 = players_salary_2019[players_salary_2019['AllStartAppearance'] == "All-Star"].reset_index(drop=True)[['Name']]
players_star_2021 = players_salary_2021[players_salary_2021['AllStartAppearance'] == "All-Star"].reset_index(drop=True)[['Name']]
players_star_2022 = players_salary_2022[players_salary_2022['AllStartAppearance'] == "All-Star"].reset_index(drop=True)[['Name']]

In [16]:
df_players = merge_players([players_star_2017, players_star_2018, players_star_2019, players_star_2021, players_star_2022])
print(df_players.shape)
df_players.head()

(129, 1)


Name
0  Paul Goldschmidt
1      Zack Greinke
2     Craig Kimbrel
3        Chris Sale
4        Wade Davis

In [17]:
df_players.to_csv(f'../data/players/players_all_star_salary_{salary_threshold}.csv', index=False)